In [0]:
from google.colab import drive
drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


# Pose Detection with OpenPose

This notebook uses an open source project [CMU-Perceptual-Computing-Lab/openpose](https://github.com/CMU-Perceptual-Computing-Lab/openpose.git) to detect/track multi person poses on a given youtube video

## Install OpenPose & motion reconstruction

In [0]:
!cp -r /content/drive/'My Drive'/motion_reconstruction /content/
#!cp -r /content/drive/'My Drive'/SfV_data /content/
!cp -r /content/drive/'My Drive'/smpl /content/
!pip2 install deepdish
!pip install deepdish
!git clone https://github.com/polmorenoc/opendr.git
!mkdir opendr3
!cp -r /content/drive/'My Drive'/opendr /content/opendr3
!cd opendr3/opendr/opendr && python setup.py build && python setup.py install
!cd /content/motion_reconstruction/models/aj_finetuned_models_170k/pose/coco/ && ln -s pose_iter_170000.caffemodel pose_iter_440000.caffemodel
!mv motion_reconstruction/models/aj_finetuned_models_170k/pose/coco/pose_deploy.prototxt motion_reconstruction/models/aj_finetuned_models_170k/pose/coco/pose_deploy_linevec.prototxt

!pip install configobj
!apt install ffmpeg
!apt-get install blender
!apt install python2.7 python-pip
!git clone https://github.com/Dene33/hmr.git
!mv models hmr/
!pip2 install -r hmr/requirements.txt
!pip2 install opendr==0.77

import os
from os.path import exists, join, basename, splitext
git_repo_url = 'https://github.com/CMU-Perceptual-Computing-Lab/openpose.git'
project_name = splitext(basename(git_repo_url))[0]
if not exists(project_name):
  # see: https://github.com/CMU-Perceptual-Computing-Lab/openpose/issues/949
  # install new CMake becaue of CUDA10
  !wget -q https://cmake.org/files/v3.13/cmake-3.13.0-Linux-x86_64.tar.gz
  !tar xfz cmake-3.13.0-Linux-x86_64.tar.gz --strip-components=1 -C /usr/local
  # clone openpose
  !git clone -q --depth 1 $git_repo_url
  !sed -i 's/execute_process(COMMAND git checkout master WORKING_DIRECTORY ${CMAKE_SOURCE_DIR}\/3rdparty\/caffe)/execute_process(COMMAND git checkout f019d0dfe86f49d1140961f8c7dec22130c83154 WORKING_DIRECTORY ${CMAKE_SOURCE_DIR}\/3rdparty\/caffe)/g' openpose/CMakeLists.txt
  # install system dependencies
  !apt-get -qq install -y libatlas-base-dev libprotobuf-dev libleveldb-dev libsnappy-dev libhdf5-serial-dev protobuf-compiler libgflags-dev libgoogle-glog-dev liblmdb-dev opencl-headers ocl-icd-opencl-dev libviennacl-dev
  # build openpose
  !cd openpose && rm -rf build || true && mkdir build && cd build && cmake .. && make -j`nproc`
!cp -r motion_reconstruction/models/aj_finetuned_models_170k/ openpose/

Run these finals lines 

In [0]:
!python /content/motion_reconstruction/run_openpose.py
!python /content/motion_reconstruction/refine_video.py
!python2 motion_reconstruction/ref_2.py

In [0]:
def show_local_mp4_video(file_name, width=640, height=480):
  import io
  import base64
  from IPython.display import HTML
  video_encoded = base64.b64encode(io.open(file_name, 'rb').read())
  return HTML(data='''<video width="{0}" height="{1}" alt="test" controls>
                        <source src="data:video/mp4;base64,{2}" type="video/mp4" />
                      </video>'''.format(width, height, video_encoded.decode('ascii')))

show_local_mp4_video('/content/SfV_data/barbell.mp4', width=960, height=720)